# Preprocessing and cleaning the try-out data

In [350]:
#Imports

import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import make_pipeline
from sklearn.compose import make_column_selector
from sklearn.compose import make_column_transformer

In [351]:
df = pd.read_csv("/Users/manonantonacci/Downloads/all_data_test2.csv")
df

Ticker  2023 Treasury Shares Number  2023 Ordinary Shares Number  \
0      BPRN                          0.0                 6.299331e+06   
1       BPT                          NaN                 2.140000e+07   
2      BPTH                          0.0                 6.176330e+05   
3     BPYPN                          NaN                          NaN   
4     BPYPO                          NaN                          NaN   
...     ...                          ...                          ...   
1776   HLTH                          NaN                 1.553048e+08   
1777   HLVX                          NaN                 4.766644e+07   
1778    HLX                          NaN                 1.522910e+08   
1779    HMC                  441263523.0                 4.993022e+09   
1780    HMN                   25911087.0                 4.083673e+07   

      2023 Share Issued  2023 Total Debt  2023 Tangible Book Value  \
0          6.299331e+06     2.428000e+07              2.299360e+08   
1          2.140000e+07              NaN              4.964000e+06   
2          6.176330e+05     1.130000e+05              4.410000e+05   
3                   NaN     7.099200e+10              6.284000e+09   
4                   NaN     7.099200e+10              6.284000e+09   
...                 ...              ...                       ...   
1776       1.553048e+08     4.793900e+07              2.306080e+08   
1777       4.766644e+07     5.119300e+07              2.655250e+08   
1778       1.522910e+08     5.405690e+08              1.496895e+09   
1779       5.434285e+09     7.665168e+12              1.031335e+13   
1780       6.674782e+07     5.460000e+08              9.641000e+08   

      2023 Invested Capital  2023 Net Tangible Assets  \
0                       NaN              2.299360e+08   
1                       NaN              4.964000e+06   
2              4.410000e+05              4.410000e+05   
3              7.849100e+10             -2.504000e+09   
4              7.849100e+10             -2.504000e+09   
...                     ...                       ...   
1776           2.502520e+08              2.306080e+08   
1777           2.907690e+08              2.655250e+08   
1778           1.862722e+09              1.496895e+09   
1779           1.884942e+13              1.031335e+13   
1780           1.721300e+09              9.641000e+08   

      2023 Capital Lease Obligations  2023 Common Stock Equity  \
0                       2.428000e+07              2.402110e+08   
1                                NaN              4.964000e+06   
2                       1.130000e+05              4.410000e+05   
3                       1.289000e+09              8.788000e+09   
4                       1.289000e+09              8.788000e+09   
...                              ...                       ...   
1776                    4.793900e+07              2.502520e+08   
1777                    2.594900e+07              2.655250e+08   
1778                    1.788470e+08              1.501000e+09   
1779                             NaN              1.118425e+13   
1780                             NaN              1.175300e+09   

      2023 Total Capitalization  2023 Total Equity Gross Minority Interest  \
0                           NaN                               2.402110e+08   
1                  4.964000e+06                               4.964000e+06   
2                  4.410000e+05                               4.410000e+05   
3                  4.886600e+10                               4.858800e+10   
4                  4.886600e+10                               4.858800e+10   
...                         ...                                        ...   
1776               2.502520e+08                               2.502520e+08   
1777               2.907690e+08                               2.655250e+08   
1778               1.814430e+09                               1.501000e+09   
1779               1.555822e+

In [352]:
df.shape

(1781, 2003)

In [353]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1781 entries, 0 to 1780
Columns: 2003 entries, Ticker to 2024 Cash Flow From Discontinued Operation
dtypes: float64(2002), object(1)
memory usage: 27.2+ MB


## Checking out NaNs

### checking NaNs per Column

In [354]:
df.isnull().sum().sort_values(ascending=False)

2024 Cash From Discontinued Operating Activities         1781
2019 Dividends Received Direct                           1781
2024 Securities Amortization                             1781
2024 Excess Tax Benefit From Stock Based Compensation    1781
2024 Unrealized Gain Loss                                1781
                                                         ... 
2022 Stockholders Equity                                    3
2022 Total Equity Gross Minority Interest                   3
2022 Common Stock Equity                                    3
2022 Net Tangible Assets                                    3
Ticker                                                      0
Length: 2003, dtype: int64

In [355]:
df.isnull().sum().sort_values(ascending=False)/len(df)

2024 Cash From Discontinued Operating Activities         1.000000
2019 Dividends Received Direct                           1.000000
2024 Securities Amortization                             1.000000
2024 Excess Tax Benefit From Stock Based Compensation    1.000000
2024 Unrealized Gain Loss                                1.000000
                                                           ...   
2022 Stockholders Equity                                 0.001684
2022 Total Equity Gross Minority Interest                0.001684
2022 Common Stock Equity                                 0.001684
2022 Net Tangible Assets                                 0.001684
Ticker                                                   0.000000
Length: 2003, dtype: float64

In [356]:
#drop columns that have more than 30% of missing data: 

def remove_shitty_columns(df):
    for column in df.columns: 
        if df[column].isnull().sum()/len(df) > 0.3:
            df.drop(columns=[column], inplace=True)
    return df

In [357]:
df = remove_shitty_columns(df)

In [358]:
df.shape

(1781, 382)

### Checking NaNs per Row

In [359]:
#Check how many NaNs per Row
df.isna().sum(axis=1).sort_values(ascending=False)

1669    300
891     294
271     290
1603    288
888     284
       ... 
662       0
925       0
1696      0
1031      0
1692      0
Length: 1781, dtype: int64

In [360]:
#check out NaNs per Row in Percentage 
df.isna().sum(axis=1).sort_values(ascending=False)/df.shape[1]

1669    0.785340
891     0.769634
271     0.759162
1603    0.753927
888     0.743455
          ...   
662     0.000000
925     0.000000
1696    0.000000
1031    0.000000
1692    0.000000
Length: 1781, dtype: float64

In [361]:
#drop rows that have more than 30% of missing values
def remove_shitty_rows(df):
    threshold = 0.3 * df.shape[1]  # Calculate the threshold for missing values
    df = df.dropna(thresh=int(df.shape[1] - threshold))
    return df


In [362]:
df = remove_shitty_rows(df)

In [363]:
df.shape

(1521, 382)

## Check for duplicates

In [364]:
df.duplicated().sum()

0

In [365]:
df

Ticker  2023 Ordinary Shares Number  2023 Share Issued  2023 Total Debt  \
0      BPRN                 6.299331e+06       6.299331e+06     2.428000e+07   
2      BPTH                 6.176330e+05       6.176330e+05     1.130000e+05   
3     BPYPN                          NaN                NaN     7.099200e+10   
4     BPYPO                          NaN                NaN     7.099200e+10   
5     BPYPP                          NaN                NaN     7.099200e+10   
...     ...                          ...                ...              ...   
1776   HLTH                 1.553048e+08       1.553048e+08     4.793900e+07   
1777   HLVX                 4.766644e+07       4.766644e+07     5.119300e+07   
1778    HLX                 1.522910e+08       1.522910e+08     5.405690e+08   
1779    HMC                 4.993022e+09       5.434285e+09     7.665168e+12   
1780    HMN                 4.083673e+07       6.674782e+07     5.460000e+08   

      2023 Tangible Book Value  2023 Invested Capital  \
0                 2.299360e+08                    NaN   
2                 4.410000e+05           4.410000e+05   
3                 6.284000e+09           7.849100e+10   
4                 6.284000e+09           7.849100e+10   
5                 6.284000e+09           7.849100e+10   
...                        ...                    ...   
1776              2.306080e+08           2.502520e+08   
1777              2.655250e+08           2.907690e+08   
1778              1.496895e+09           1.862722e+09   
1779              1.031335e+13           1.884942e+13   
1780              9.641000e+08           1.721300e+09   

      2023 Net Tangible Assets  2023 Common Stock Equity  \
0                 2.299360e+08              2.402110e+08   
2                 4.410000e+05              4.410000e+05   
3                -2.504000e+09              8.788000e+09   
4                -2.504000e+09              8.788000e+09   
5                -2.504000e+09              8.788000e+09   
...                        ...                       ...   
1776              2.306080e+08              2.502520e+08   
1777              2.655250e+08              2.655250e+08   
1778              1.496895e+09              1.501000e+09   
1779              1.031335e+13              1.118425e+13   
1780              9.641000e+08              1.175300e+09   

      2023 Total Capitalization  2023 Total Equity Gross Minority Interest  \
0                           NaN                               2.402110e+08   
2                  4.410000e+05                               4.410000e+05   
3                  4.886600e+10                               4.858800e+10   
4                  4.886600e+10                               4.858800e+10   
5                  4.886600e+10                               4.858800e+10   
...                         ...                                        ...   
1776               2.502520e+08                               2.502520e+08   
1777               2.907690e+08                               2.655250e+08   
1778               1.814430e+09                               1.501000e+09   
1779               1.555822e+13                               1.150229e+13   
1780               1.721300e+09                               1.175300e+09   

      2023 Stockholders Equity  2023 Retained Earnings  \
0                 2.402110e+08            1.494140e+08   
2                 4.410000e+05           -1.076070e+08   
3                 0.000000e+00           -9.350000e+08   
4                 0.000000e+00           -9.350000e+08   
5                 0.000000e+00           -9.350000e+08   
...                        ...                     ...   
1776              2.502520e+08           -5.915380e+08   
1777              2.655250e+08           -3.885590e+08   
1778              1.501000e+09            3.124500e+08   
1779              1.118425e+13            9.980128e+12   
1780              1.175300e+09            1.502200e+09   

    

In [366]:
df.columns

Index(['Ticker', '2023 Ordinary Shares Number', '2023 Share Issued',
       '2023 Total Debt', '2023 Tangible Book Value', '2023 Invested Capital',
       '2023 Net Tangible Assets', '2023 Common Stock Equity',
       '2023 Total Capitalization',
       '2023 Total Equity Gross Minority Interest',
       ...
       '2023 Long Term Debt Payments', '2022 Net Long Term Debt Issuance',
       '2022 Long Term Debt Payments', '2022 Long Term Debt Issuance',
       '2021 Net Long Term Debt Issuance', '2021 Long Term Debt Payments',
       '2021 Long Term Debt Issuance', '2020 Net Long Term Debt Issuance',
       '2020 Long Term Debt Payments', '2020 Long Term Debt Issuance'],
      dtype='object', length=382)

In [367]:
pd.set_option('display.max_columns', None)
df.head(30)

Ticker  2023 Ordinary Shares Number  2023 Share Issued  2023 Total Debt  \
0    BPRN                 6.299331e+06       6.299331e+06     2.428000e+07   
2    BPTH                 6.176330e+05       6.176330e+05     1.130000e+05   
3   BPYPN                          NaN                NaN     7.099200e+10   
4   BPYPO                          NaN                NaN     7.099200e+10   
5   BPYPP                          NaN                NaN     7.099200e+10   
6      BQ                 6.880081e+07       6.880081e+07     2.095490e+08   
7      BR                 1.181000e+08       1.545000e+08     3.652600e+09   
8    BRAG                 2.300355e+07       2.300355e+07     3.277000e+06   
9    BRBR                 1.312454e+08       1.365539e+08     8.568000e+08   
10   BRBS                 1.919838e+07       1.919838e+07     2.594740e+08   
11    BRC                 4.854735e+07       5.480012e+07     8.065900e+07   
12   BRCC                 6.563781e+07       6.563781e+07     1.092390e+08   
13   BRDG                 3.782989e+07       3.782989e+07     4.839520e+08   
14   BREA                          NaN                NaN              NaN   
17   BRFH                 1.442010e+07       1.442010e+07     0.000000e+00   
18   BRFS                 1.678656e+09       1.682473e+09     2.381740e+10   
19   BRID                 9.076832e+06       9.076832e+06     7.491000e+06   
23   BRKL                 8.964368e+07       9.699808e+07     1.408668e+09   
24   BRKR                 1.451648e+08       1.759437e+08     1.379600e+09   
27   BRLT                 1.252215e+07       1.252215e+07     1.002010e+08   
28    BRN                 9.990778e+06       1.015868e+07     4.700000e+04   
29   BRNS                 3.864354e+07       3.864354e+07     1.297600e+07   
30    BRO                 2.846000e+08       3.043000e+08     4.019600e+09   
31   BROG                          NaN                NaN              NaN   
32   BROS                 8.062700e+07       8.062700e+07     6.765810e+08   
35   BRSP                 1.299851e+08       1.299851e+08     2.738912e+09   
36    BRT                 1.753600e+07       1.753600e+07     4.595700e+08   
37   BRTX                 4.706917e+06       4.706917e+06              NaN   
38    BRX                 3.005964e+08       3.097234e+08     4.933525e+09   
39    BRY                 7.566743e+07       8.767124e+07     4.309370e+08   

    2023 Tangible Book Value  2023 Invested Capital  2023 Net Tangible Assets  \
0               2.299360e+08                    NaN              2.299360e+08   
2               4.410000e+05           4.410000e+05              4.410000e+05   
3               6.284000e+09           7.849100e+10             -2.504000e+09   
4               6.284000e+09           7.849100e+10             -2.504000e+09   
5               6.284000e+09           7.849100e+10             -2.504000e+09   
6               1.566890e+08           3.658710e+08              1.566890e+08   
7              -2.688200e+09           5.653800e+09             -2.688200e+09   
8               1.930000e+05           7.024700e+07              1.930000e+05   
9              -5.662000e+08           5.333000e+08             -5.662000e+08   
10              1.534930e+08           4.358440e+08              1.534930e+08   
11              3.361770e+08           1.040635e+09              3.361770e+08   
12              1.285300e+07           8.425100e+07              1.285300e+07   
13             -2.988690e+08           5.588650e+08             -2.988690e+08   
14                       NaN                    NaN                       NaN   
17              2.262000e+06           2.503000e+06              2.262000e+06   
18              8.782990e+09           3.501898e+10              8.782990e+09   
19              1.295350e+08           1.333660e+08              1.295350e+08   
23              9.332150e+08           2.575314e+09              9.332150e+08   
24              4.641000e+08           2.6587

## Replace remaining missing values with 0s

In [368]:
#use simple impute with strategy = "constant"
imputer = SimpleImputer(strategy="constant", fill_value=0) 


## Scaling our data with Robust Scaler

In [369]:
df.Ticker.info()

<class 'pandas.core.series.Series'>
Index: 1521 entries, 0 to 1780
Series name: Ticker
Non-Null Count  Dtype 
--------------  ----- 
1521 non-null   object
dtypes: object(1)
memory usage: 23.8+ KB


In [370]:
df.Ticker.dtype

dtype('O')

In [371]:
rb_scaler = RobustScaler()

In [372]:
num_transformer = make_pipeline(imputer, rb_scaler)
num_columns = make_column_selector(dtype_exclude="object")


In [373]:
#Create Preproc Pipeline
preproc_basic = make_column_transformer((num_transformer, num_columns))

In [374]:
#Apply Preprocessing to dataframe
preprocessed_data = preproc_basic.fit_transform(df)

# Get your features' names
preproc_basic.get_feature_names_out()

#Change column names of transformed dataframe 
df_preproc = pd.DataFrame(
    preprocessed_data,
    columns=preproc_basic.get_feature_names_out()
)


In [375]:
df_preproc

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                 -0.334573                    -0.336893   
1                                 -0.374646                    -0.374069   
2                                 -0.379003                    -0.378111   
3                                 -0.379003                    -0.378111   
4                                 -0.379003                    -0.378111   
...                                     ...                          ...   
1516                               0.716363                     0.638076   
1517                              -0.042811                    -0.066221   
1518                               0.695107                     0.618356   
1519                              34.836812                    35.179385   
1520                              -0.090981                     0.058632   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                     -0.139878                            0.120693   
1                     -0.154251                           -0.175043   
2                     42.066962                            7.922191   
3                     42.066962                            7.922191   
4                     42.066962                            7.922191   
...                         ...                                 ...   
1516                  -0.125807                            0.121559   
1517                  -0.123872                            0.166554   
1518                   0.167176                            1.753344   
1519                4558.573477                        13290.001228   
1520                   0.170406                            1.066764   

      pipeline__2023 Invested Capital  pipeline__2023 Net Tangible Assets  \
0                           -0.217367                            0.132975   
1                           -0.217238                           -0.169798   
2                           22.697914                           -3.473915   
3                           22.697914                           -3.473915   
4                           22.697914                           -3.473915   
...                               ...                                 ...   
1516                        -0.144306                            0.133862   
1517                        -0.132477                            0.179928   
1518                         0.326451                            1.804478   
1519                      5502.830131                        13606.263069   
1520                         0.285163                            1.101560   

      pipeline__2023 Common Stock Equity  pipeline__2023 Total Capitalization  \
0                              -0.074506                            -0.208220   
1                              -0.202167                            -0.208087   
2                               4.476604                            14.595410   
3                               4.476604                            14.595410   
4                               4.476604                            14.595410   
...                                  ...                                  ...   
1516                           -0.069160                            -0.132408   
1517                           -0.061028                            -0.120134   
1518                            0.596778                             0.341449   
1519                         5954.641045                          4713.052247   
1520                            0.423365                             0.313236   

      pipeline__2023 Total Equity Gross Minority Interest  \
0                                             -0.082341     
1                                             -0.202575     
2                                             24.161969     
3                                             24.161969     
4                                    

In [376]:
df

Ticker  2023 Ordinary Shares Number  2023 Share Issued  2023 Total Debt  \
0      BPRN                 6.299331e+06       6.299331e+06     2.428000e+07   
2      BPTH                 6.176330e+05       6.176330e+05     1.130000e+05   
3     BPYPN                          NaN                NaN     7.099200e+10   
4     BPYPO                          NaN                NaN     7.099200e+10   
5     BPYPP                          NaN                NaN     7.099200e+10   
...     ...                          ...                ...              ...   
1776   HLTH                 1.553048e+08       1.553048e+08     4.793900e+07   
1777   HLVX                 4.766644e+07       4.766644e+07     5.119300e+07   
1778    HLX                 1.522910e+08       1.522910e+08     5.405690e+08   
1779    HMC                 4.993022e+09       5.434285e+09     7.665168e+12   
1780    HMN                 4.083673e+07       6.674782e+07     5.460000e+08   

      2023 Tangible Book Value  2023 Invested Capital  \
0                 2.299360e+08                    NaN   
2                 4.410000e+05           4.410000e+05   
3                 6.284000e+09           7.849100e+10   
4                 6.284000e+09           7.849100e+10   
5                 6.284000e+09           7.849100e+10   
...                        ...                    ...   
1776              2.306080e+08           2.502520e+08   
1777              2.655250e+08           2.907690e+08   
1778              1.496895e+09           1.862722e+09   
1779              1.031335e+13           1.884942e+13   
1780              9.641000e+08           1.721300e+09   

      2023 Net Tangible Assets  2023 Common Stock Equity  \
0                 2.299360e+08              2.402110e+08   
2                 4.410000e+05              4.410000e+05   
3                -2.504000e+09              8.788000e+09   
4                -2.504000e+09              8.788000e+09   
5                -2.504000e+09              8.788000e+09   
...                        ...                       ...   
1776              2.306080e+08              2.502520e+08   
1777              2.655250e+08              2.655250e+08   
1778              1.496895e+09              1.501000e+09   
1779              1.031335e+13              1.118425e+13   
1780              9.641000e+08              1.175300e+09   

      2023 Total Capitalization  2023 Total Equity Gross Minority Interest  \
0                           NaN                               2.402110e+08   
2                  4.410000e+05                               4.410000e+05   
3                  4.886600e+10                               4.858800e+10   
4                  4.886600e+10                               4.858800e+10   
5                  4.886600e+10                               4.858800e+10   
...                         ...                                        ...   
1776               2.502520e+08                               2.502520e+08   
1777               2.907690e+08                               2.655250e+08   
1778               1.814430e+09                               1.501000e+09   
1779               1.555822e+13                               1.150229e+13   
1780               1.721300e+09                               1.175300e+09   

      2023 Stockholders Equity  2023 Retained Earnings  \
0                 2.402110e+08            1.494140e+08   
2                 4.410000e+05           -1.076070e+08   
3                 0.000000e+00           -9.350000e+08   
4                 0.000000e+00           -9.350000e+08   
5                 0.000000e+00           -9.350000e+08   
...                        ...                     ...   
1776              2.502520e+08           -5.915380e+08   
1777              2.655250e+08           -3.885590e+08   
1778              1.501000e+09            3.124500e+08   
1779              1.118425e+13            9.980128e+12   
1780              1.175300e+09            1.502200e+09   

    

In [378]:
#we now need to add back in the ticker labels
#first reset index of original df
df = df.reset_index(drop=True)

#Merge with tickers
df_preproc = df_preproc.join(df.Ticker)
df_preproc


pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                 -0.334573                    -0.336893   
1                                 -0.374646                    -0.374069   
2                                 -0.379003                    -0.378111   
3                                 -0.379003                    -0.378111   
4                                 -0.379003                    -0.378111   
...                                     ...                          ...   
1516                               0.716363                     0.638076   
1517                              -0.042811                    -0.066221   
1518                               0.695107                     0.618356   
1519                              34.836812                    35.179385   
1520                              -0.090981                     0.058632   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                     -0.139878                            0.120693   
1                     -0.154251                           -0.175043   
2                     42.066962                            7.922191   
3                     42.066962                            7.922191   
4                     42.066962                            7.922191   
...                         ...                                 ...   
1516                  -0.125807                            0.121559   
1517                  -0.123872                            0.166554   
1518                   0.167176                            1.753344   
1519                4558.573477                        13290.001228   
1520                   0.170406                            1.066764   

      pipeline__2023 Invested Capital  pipeline__2023 Net Tangible Assets  \
0                           -0.217367                            0.132975   
1                           -0.217238                           -0.169798   
2                           22.697914                           -3.473915   
3                           22.697914                           -3.473915   
4                           22.697914                           -3.473915   
...                               ...                                 ...   
1516                        -0.144306                            0.133862   
1517                        -0.132477                            0.179928   
1518                         0.326451                            1.804478   
1519                      5502.830131                        13606.263069   
1520                         0.285163                            1.101560   

      pipeline__2023 Common Stock Equity  pipeline__2023 Total Capitalization  \
0                              -0.074506                            -0.208220   
1                              -0.202167                            -0.208087   
2                               4.476604                            14.595410   
3                               4.476604                            14.595410   
4                               4.476604                            14.595410   
...                                  ...                                  ...   
1516                           -0.069160                            -0.132408   
1517                           -0.061028                            -0.120134   
1518                            0.596778                             0.341449   
1519                         5954.641045                          4713.052247   
1520                            0.423365                             0.313236   

      pipeline__2023 Total Equity Gross Minority Interest  \
0                                             -0.082341     
1                                             -0.202575     
2                                             24.161969     
3                                             24.161969     
4                                    

In [379]:
df_preproc.Ticker.isna().sum()

0